# imports

In [2]:
from langchain_ollama import ChatOllama
from langchain_core.prompts import ChatPromptTemplate

import logging
import os
from rdflib import Graph

# logging

In [3]:
logger = logging.getLogger(__name__)
logging.basicConfig(level=logging.INFO) 

# initialize LLM model

In [4]:
chat_ollama = ChatOllama(model="gemma3:4b", temperature=0)
chat_ollama

ChatOllama(model='gemma3:4b', temperature=0.0)

# Chat Prompt

In [28]:
from langchain.prompts import ChatPromptTemplate

sparql_prompt = ChatPromptTemplate.from_messages([
    ("system", """You are a SPARQL query generator.

You will use the following named graphs in the SPARQL query:
- Ontology Graph: <{ontology_graph}>
- Data Graph: <{data_graph}>

Given the Ontology:
{ontology}

Understand the core elements such as:
- Classes
- Object Properties
- Data Properties
- Annotation Properties
- Relationships between classes
- The complete structure of the Ontology

Your tasks:
1. Summarize what domain the ontology covers.
2. Suggest the types of questions users can ask based on it.
3. Based on the user's question below, generate a valid SPARQL query.
4. Ensure the query conforms to the ontology’s structure.
5. Use the `FROM` clause with the provided named graphs.
6. Output **only the SPARQL query**, unless explicitly asked otherwise.

Here are some examples of questions and their SPARQL equivalents:
{examples}

The user’s question is:
{question}
""")
])


In [29]:
def load_ttl_as_string(file_path):
    g = Graph()
    g.parse(file_path, format="turtle")  # ← Input is Turtle (.ttl)
    return g.serialize(format="nt") 

In [30]:
ontology_file = r"C:\Users\deepa\data\workspace\notebooks\datasets\dbpedia-14-04-2025-ontology\ontology_type=parsed.ttl"
ontology_triples = load_ttl_as_string(ontology_file)
# ontology_triples

In [31]:
few_shot_example_file = r"C:\Users\deepa\data\workspace\notebooks\datasets\few-shot-example\few_shot_example.txt"
with open(few_shot_example_file, "r", encoding="utf-8") as f:
    few_shot_examples = f.read()

In [32]:
formatted_messages = sparql_prompt.format_messages(
    ontology=ontology_triples,
    examples=few_shot_examples,
    ontology_graph="https://www.sw.org/dbpedia/ontology",
    data_graph="https://www.sw.org/dbpedia/data",
    question="Who is the director of Inception?"
)
for msg in formatted_messages:
    print(f"{msg.type}: {msg.content}\n{'-'*80}")

system: You are a SPARQL query generator.

You will use the following named graphs in the SPARQL query:
- Ontology Graph: <https://www.sw.org/dbpedia/ontology>
- Data Graph: <https://www.sw.org/dbpedia/data>

Given the Ontology:
<http://dbpedia.org/ontology/> <http://open.vocab.org/terms/defines> <http://dbpedia.org/ontology/routeStart> .
<http://dbpedia.org/ontology/complexion> <http://www.w3.org/2000/01/rdf-schema#isDefinedBy> <http://dbpedia.org/ontology/> .
<http://dbpedia.org/ontology/سومو_پہلوان> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type> <http://www.w3.org/2002/07/owl#Class> .
<http://dbpedia.org/ontology/> <http://open.vocab.org/terms/defines> <http://dbpedia.org/ontology/Academic> .
<http://dbpedia.org/ontology/Pyramid> <http://www.w3.org/2000/01/rdf-schema#label> "Pyramide"@de .
<http://dbpedia.org/ontology/> <http://open.vocab.org/terms/defines> <http://dbpedia.org/ontology/railGauge> .
<http://dbpedia.org/ontology/data/definitions.ttl> <http://open.vocab.org/terms/de

In [33]:
response = chat_ollama.invoke(formatted_messages)

INFO:httpx:HTTP Request: POST http://127.0.0.1:11434/api/chat "HTTP/1.1 200 OK"


In [34]:
print(response)

content='```sparql\nPREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>\nPREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>\nPREFIX dbo: <http://dbpedia.org/ontology/>\nPREFIX foaf: <http://xmlns.com/foaf/0.1/>\n\nSELECT ?director ?label\nWHERE {\n  ?film rdf:type dbo:Film .\n  ?film dbo:director ?director .\n\n  OPTIONAL { ?film rdfs:label ?rdfsLabel . }\n  OPTIONAL { ?film foaf:name ?foafName . }\n\n  BIND(COALESCE(?rdfsLabel, ?foafName) AS ?label)\n\n  FILTER (\n    LANG(?label) = "en" &&\n    CONTAINS(LCASE(STR(?label)), LCASE(STR("Inception")))\n  )\n}\n```' additional_kwargs={} response_metadata={'model': 'gemma3:4b', 'created_at': '2025-05-24T17:15:40.4877159Z', 'done': True, 'done_reason': 'stop', 'total_duration': 14771684000, 'load_duration': 3924736900, 'prompt_eval_count': 4096, 'prompt_eval_duration': 7403443600, 'eval_count': 217, 'eval_duration': 3322260200, 'message': Message(role='assistant', content='', images=None, tool_calls=None)} id='run-a833ad04-931d-4295

In [35]:
print(response.content)

```sparql
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX dbo: <http://dbpedia.org/ontology/>
PREFIX foaf: <http://xmlns.com/foaf/0.1/>

SELECT ?director ?label
WHERE {
  ?film rdf:type dbo:Film .
  ?film dbo:director ?director .

  OPTIONAL { ?film rdfs:label ?rdfsLabel . }
  OPTIONAL { ?film foaf:name ?foafName . }

  BIND(COALESCE(?rdfsLabel, ?foafName) AS ?label)

  FILTER (
    LANG(?label) = "en" &&
    CONTAINS(LCASE(STR(?label)), LCASE(STR("Inception")))
  )
}
```
